In [41]:
import numpy as np
import pathlib
import pandas as pd
import matplotlib.pyplot as plt
from importlib import reload 



from ics.cobraCharmer import pfiDesign
from opdb import opdb
from ics.cobraCharmer import func

from procedures.moduleTest import visDianosticPlot
reload(visDianosticPlot)

<module 'procedures.moduleTest.visDianosticPlot' from '/software/devel/pfs/ics_cobraCharmer/python/procedures/moduleTest/visDianosticPlot.py'>

In [42]:
xml=pathlib.Path('/software/devel/pfs/pfs_instdata/data/pfi/modules/ALL/ALL_final_20210920_mm.xml')
model = pfiDesign.PFIDesign(xml)


centers=model.centers

In [43]:
cobras = []
for i in model.findAllCobras():
    c = func.Cobra(model.moduleIds[i],
                   model.positionerIds[i])
    cobras.append(c)
allCobras = np.array(cobras)
nCobras = len(allCobras)

goodNums = [i+1 for i,c in enumerate(allCobras) if
           model.cobraIsGood(c.cobraNum, c.module)]
badNums = [e for e in range(1, nCobras+1) if e not in goodNums]


goodIdx = np.array(goodNums, dtype='i4') - 1
badIdx = np.array(badNums, dtype='i4') - 1



In [44]:
reload(visDianosticPlot)
vis=visDianosticPlot.VisDianosticPlot(xml=xml)

# Plotting all cobras at the safe location

In [26]:
cobraIdx = np.arange(2394)
theta=np.full(2394,np.deg2rad(210))
theta[cobraIdx>798] -= np.pi*2/3
theta[cobraIdx>=1596] -= np.pi*2/3

phi = np.full(2394,np.deg2rad(60))

%matplotlib widget
vis.visCreateNewPlot('theta MM', 'X', 'Y')
vis.visGeometryFromXML(xml, thetaAngle=theta, phiAngle=phi, patrol=True)

vis.visDotLocation()
#vis.visPauseExecution()




Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

# Loading DOT locations

In [27]:
dotFile = '/software/devel/pfs/pfs_instdata/data/pfi/dot/black_dots_mm.csv'
dotDF=pd.read_csv(dotFile)

dotCenter=dotDF['x']+dotDF['y']*1j

In [28]:
from ics.cobraCharmer import pfi as pfiControl

p=pfiControl.PFI(doLoadModel=False,doConnect=False)
p.loadModel([xml])

2022-01-13T23:10:22.533 20 pfi        pfi.py:91 load cobra model from [PosixPath('/software/devel/pfs/pfs_instdata/data/pfi/modules/ALL/ALL_final_20210920_mm.xml')]


In [39]:

# Use dot center as target to calculate the phi and theta angle
targets=(dotDF['x'].values)+(dotDF['y'].values)*1j
cobras = p.getAllDefinedCobras()
thetaSolution, phiSolution, flags=p.positionsToAngles(cobras, targets)

# Move theta 30 degree away, the solution is alway from hard-stop
thataMove=thetaSolution[:,0]+np.deg2rad(60)+model.tht0
phiMove = phiSolution[:,0]

pos=p.anglesToPositions(cobras,thataMove,phiMove)
pos[badIdx] = centers[badIdx]



2022-01-13T23:23:36.045 40 pfi        pfi.py:896 Some theta angles are out of range
2022-01-13T23:23:36.046 40 pfi        pfi.py:899 Some phi angles are out of range


In [40]:
%matplotlib widget
vis.visCreateNewPlot('theta MM', 'X', 'Y')
vis.visGeometryFromXML(xml, thetaAngle=thataMove, phiAngle=phiMove, patrol=True)

vis.visDotLocation()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

/software/devel/pfs/ics_cobraCharmer/python/ics/cobraCharmer/pfiDesign.py:286: RuntimeWarning: divide by zero encountered in true_divide
  self.S1Nm[i] = angularStep / np.array(list(map(float, slowJoint1Rev)))
/software/devel/pfs/ics_cobraCharmer/python/ics/cobraCharmer/pfiDesign.py:288: RuntimeWarning: divide by zero encountered in true_divide
  self.S2Nm[i] = angularStep / np.array(list(map(float, slowJoint2Rev)))
/software/devel/pfs/ics_cobraCharmer/python/ics/cobraCharmer/pfiDesign.py:290: RuntimeWarning: divide by zero encountered in true_divide
  self.F1Nm[i] = angularStep / np.array(list(map(float, fastJoint1Rev)))


In [51]:
df = {
    'cobra_id':np.arange(2394)+1,
    'x_pos':pos.real,
    'y_pos':pos.imag
}

data = pd.DataFrame(df)
data.to_csv('theta_cross.csv')